# IBM Applied Data Science Capstone Course by Coursera

## Week 5 Final Project

### Opening a new  Indian Restaurant in Hyderabad,India
* Build a  dataframe of neighborhoods in Hyderabad,india by web scraping from wiki page
* Get Geographical coordinates of these neighborhoods 
* Explore  venues in each neighborhood using FourSquareAPI
* Cluster these neighborhoods 
* Find the best cluster to open a new Indian Restaurant

# Scrap content from wiki page
##  import libraries

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option("display.max_columns", None)
pd.set_option("display.max_rows", None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes
!conda install -c conda-forge geocoder --yes
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
import geocoder# to get coordinates

import requests # library to handle requests
from bs4 import BeautifulSoup # library to parse HTML and XML documents

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes
import folium # map rendering library

print("Libraries imported.")

Solving environment: ...working... done

# All requested packages already installed.

Solving environment: ...working... done

# All requested packages already installed.

Solving environment: ...working... done

# All requested packages already installed.

Libraries imported.


## scrap data from wiki page 

In [2]:
data = requests.get("https://en.wikipedia.org/wiki/Category:Neighbourhoods_in_Hyderabad,_India").text
soup = BeautifulSoup(data, 'html.parser')

neighborhoodList = []


for row in soup.find_all("div", class_="mw-category")[0].findAll("li"):
    neighborhoodList.append(row.text)
    

hyd_df = pd.DataFrame({"Neighborhood": neighborhoodList})

hyd_df.head()

Neighborhood
0  A. S. Rao Nagar
1      A.C. Guards
2  Abhyudaya Nagar
3            Abids
4          Adikmet

In [3]:
hyd_df.shape

(200, 1)

## Get the geographical coordinates

In [4]:
# define a function to get coordinates
def get_latlng(neighborhood):
    # initialize your variable to None
    lat_lng_coords = None
    # loop until you get the coordinates
    while(lat_lng_coords is None):
        g = geocoder.arcgis('{}, Hyderabad,India'.format(neighborhood))
        lat_lng_coords = g.latlng
    return lat_lng_coords

In [8]:
coords=[get_latlng(neighborhood) for neighborhood in hyd_df["Neighborhood"].to_list()]

In [9]:
coords

[[17.411200000000065, 78.50824000000006],
 [17.392977027745946, 78.45686724051741],
 [17.337650000000053, 78.56414000000007],
 [17.389800000000037, 78.47658000000007],
 [17.410610000000077, 78.51513000000006],
 [17.37751000000003, 78.48005000000006],
 [17.387364823969637, 78.4669870622138],
 [17.34259000000003, 78.47626000000008],
 [17.36068000000006, 78.47998000000007],
 [17.503370000000075, 78.41602000000006],
 [17.535430000000076, 78.54427000000004],
 [17.385820000000024, 78.51836000000003],
 [17.435350000000028, 78.44861000000003],
 [17.40784000000002, 78.49150000000003],
 [17.385140000000035, 78.44738000000007],
 [17.369170000000054, 78.43683000000004],
 [17.40710000000007, 78.50233000000003],
 [17.372720000000072, 78.49047000000007],
 [17.38897000000003, 78.48681000000005],
 [17.39931000000007, 78.49964000000006],
 [17.339920000000063, 78.54553000000004],
 [17.448510000000056, 78.44924000000003],
 [17.415350000000046, 78.43435000000005],
 [17.38859199570786, 78.47665099785392],
 

In [12]:
df_coords=pd.DataFrame(data=coords,columns=['Latitude','Longitude'])


In [26]:
hyd_df["Latitude"]=df_coords["Latitude"]
hyd_df["Longitude"]=df_coords["Longitude"]
print(hyd_df.shape)


hyd_df


(200, 3)


Neighborhood   Latitude  Longitude
0                         A. S. Rao Nagar  17.411200  78.508240
1                             A.C. Guards  17.392977  78.456867
2                         Abhyudaya Nagar  17.337650  78.564140
3                                   Abids  17.389800  78.476580
4                                 Adikmet  17.410610  78.515130
5                              Afzal Gunj  17.377510  78.480050
6                                Aghapura  17.387365  78.466987
7                      Aliabad, Hyderabad  17.342590  78.476260
8                            Alijah Kotla  17.360680  78.479980
9                           Allwyn Colony  17.503370  78.416020
10                                  Alwal  17.535430  78.544270
11                               Amberpet  17.385820  78.518360
12                               Ameerpet  17.435350  78.448610
13                 Ashok Nagar, Hyderabad  17.407840  78.491500
14                             Asif Nagar  17.385140  78.447380
15                                Attapur  17.369170  78.436830
16                    Azamabad, Hyderabad  17.407100  78.502330
17                               Azampura  17.372720  78.490470
18                             Badichowdi  17.388970  78.486810
19                       Bagh Lingampally  17.399310  78.499640
20                           Bairamalguda  17.339920  78.545530
21                              Balkampet  17.448510  78.449240
22                          Banjara Hills  17.415350  78.434350
23                 Bank Street, Hyderabad  17.388592  78.476651
24                      Barkas, Hyderabad  17.315940  78.481070
25                             Barkatpura  17.393210  78.499220
26                            Basheerbagh  17.402110  78.477700
27                              Bazarghat  17.398103  78.462720
28                           Begum Bazaar  17.373500  78.469050
29                               Begumpet  17.447290  78.453960
30                           Bharat Nagar  17.528340  78.525040
31               BHEL Township, Hyderabad  17.505990  78.304540
32                              BJR Nagar  17.412570  78.405190
33                            Boggulkunta  17.391370  78.480230
34                              Borabanda  17.452700  78.412560
35                             Bowenpally  17.469115  78.489889
36                          Brahman Vaadi  17.378050  78.514450
37                             Chaderghat  17.377330  78.489740
38                              Champapet  17.347670  78.515520
39                           Chanchalguda  17.369180  78.495570
40                       Chandrayan Gutta  17.315820  78.477640
41                          Chatta Bazaar  17.370160  78.478050
42                            Cherlapally  17.466480  78.599990
43                           Chikkadpally  17.403010  78.497920
44                            Chilkalguda  17.426750  78.512290
45                          Chintal Basti  17.406620  78.456590
46                          Chintalakunta  17.338620  78.557410
47                              Dabirpura  17.366180  78.487360
48                           Dar-ul-Shifa  17.372000  78.484740
49                               Dhoolpet  17.374070  78.459920
50                           Dilsukhnagar  17.368570  78.535150
51                              Domalguda  17.409950  78.482290
52                         ECIL 'X' Roads  17.252669  78.378976
53                              Edi Bazar  17.344520  78.494190
54                              Erragadda  17.453330  78.430340
55                 Fateh Nagar, Hyderabad  17.458410  78.451810
56                              Ferozguda  17.474120  78.426387
57                             Film Nagar  17.413910  78.405470
58                             Gachibowli  17.431810  78.386360
59                           Gaddiannaram  17.365000  78.526180
60                                Golnaka  17.391920  78.505640
61                             Goshamahal  17.382100  78.4706

In [14]:
hyd_df.to_csv("hyd_df.csv", index=False)


## create a map of hyderabad and plot its neighborhoods

In [17]:
address='Hyderabad,India'

geolocator=Nominatim(user_agent="My application")
location=geolocator.geocode(address)
latitude=location.latitude
longitude=location.longitude

print("latitude and longitude of hyderabad are {},{}.".format(latitude,longitude))

latitude and longitude of hyderabad are 17.38878595,78.46106473453146.


In [30]:
map_hyd=folium.Map(location=[latitude,longitude],zoom_start=11)

for lat,lng,label in zip(hyd_df["Latitude"],hyd_df["Longitude"],hyd_df["Neighborhood"]):
    label='{}'.format("Neighborhood")
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker([lat,lng],popup=label,radius=5,color='blue',fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_hyd)
    
map_hyd
    

In [31]:
map_hyd.save('map_hyd.html')


## Use the foursquare api to explore neighborhoods

In [32]:

# define Foursquare Credentials and Version
CLIENT_ID = 'UQJR1KS03F4QQJG3EJJPVMOICO5VF2MA2ETIFDIJBCQPBVR0' # your Foursquare ID
CLIENT_SECRET = 'UP5S0DRNJANZZM3PRCWOSUUZVD433SQRQVB0BNVHQQVM0IME' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: UQJR1KS03F4QQJG3EJJPVMOICO5VF2MA2ETIFDIJBCQPBVR0
CLIENT_SECRET:UP5S0DRNJANZZM3PRCWOSUUZVD433SQRQVB0BNVHQQVM0IME


In [33]:
LIMIT = 100
radius = 2000

venues = []

for lat, long, neighborhood in zip(hyd_df['Latitude'], hyd_df['Longitude'], hyd_df['Neighborhood']):
    
    # create the API request URL
    url = "https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}".format(
        CLIENT_ID,
        CLIENT_SECRET,
        VERSION,
        lat,
        long,
        radius, 
        LIMIT)
    
    # make the GET request
    results = requests.get(url).json()["response"]['groups'][0]['items']
    
    # return only relevant information for each nearby venue
    for venue in results:
        venues.append((
            neighborhood,
            lat, 
            long, 
            venue['venue']['name'], 
            venue['venue']['location']['lat'], 
            venue['venue']['location']['lng'],  
            venue['venue']['categories'][0]['name']))

In [56]:
venues_df=pd.DataFrame(venues,columns=['Neighborhood','Latitude','Longitude','Venuename','VenueLatitude','VenueLongitude','VenueCategory'])
venues_df

Neighborhood   Latitude  Longitude  \
0                          A. S. Rao Nagar  17.411200  78.508240   
1                          A. S. Rao Nagar  17.411200  78.508240   
2                          A. S. Rao Nagar  17.411200  78.508240   
3                          A. S. Rao Nagar  17.411200  78.508240   
4                          A. S. Rao Nagar  17.411200  78.508240   
5                          A. S. Rao Nagar  17.411200  78.508240   
6                          A. S. Rao Nagar  17.411200  78.508240   
7                          A. S. Rao Nagar  17.411200  78.508240   
8                          A. S. Rao Nagar  17.411200  78.508240   
9                          A. S. Rao Nagar  17.411200  78.508240   
10                         A. S. Rao Nagar  17.411200  78.508240   
11                         A. S. Rao Nagar  17.411200  78.508240   
12                         A. S. Rao Nagar  17.411200  78.508240   
13                         A. S. Rao Nagar  17.411200  78.508240   
14                         A. S. Rao Nagar  17.411200  78.508240   
15                         A. S. Rao Nagar  17.411200  78.508240   
16                         A. S. Rao Nagar  17.411200  78.508240   
17                         A. S. Rao Nagar  17.411200  78.508240   
18                         A. S. Rao Nagar  17.411200  78.508240   
19                         A. S. Rao Nagar  17.411200  78.508240   
20                         A. S. Rao Nagar  17.411200  78.508240   
21                         A. S. Rao Nagar  17.411200  78.508240   
22                         A. S. Rao Nagar  17.411200  78.508240   
23                         A. S. Rao Nagar  17.411200  78.508240   
24                             A.C. Guards  17.392977  78.456867   
25                             A.C. Guards  17.392977  78.456867   
26                             A.C. Guards  17.392977  78.456867   
27                             A.C. Guards  17.392977  78.456867   
28                             A.C. Guards  17.392977  78.456867   
29                             A.C. Guards  17.392977  78.456867   
30                             A.C. Guards  17.392977  78.456867   
31                             A.C. Guards  17.392977  78.456867   
32                             A.C. Guards  17.392977  78.456867   
33                             A.C. Guards  17.392977  78.456867   
34                             A.C. Guards  17.392977  78.456867   
35                             A.C. Guards  17.392977  78.456867   
36                             A.C. Guards  17.392977  78.456867   
37                             A.C. Guards  17.392977  78.456867   
38                             A.C. Guards  17.392977  78.456867   
39                             A.C. Guards  17.392977  78.456867   
40                             A.C. Guards  17.392977  78.456867   
41                             A.C. Guards  17.392977  78.456867   
42                             A.C. Guards  17.392977  78.456867   
43                             A.C. Guards  17.392977  78.456867   
44                             A.C. Guards  17.392977  78.456867   
45                             A.C. Guards  17.392977  78.456867   
46                             A.C. Guards  17.392977  78.456867   
47                             A.C. Guards  17.392977  78.456867   
48                             A.C. Guards  17.392977  78.456867   
49                             A.C. Guards  17.392977  78.456867   
50                             A.C. Guards  17.392977  78.456867   
51                             A.C. Guards  17.392977  78.456867   
52                             A.C. Guards  17.392977  78.456867   
53                             A.C. Guards  17.392977  78.456867   
54                             A.C. Guards  17.392977  78.456867   
55                             A.C. Guards  17.392977  78.456867   
56                             A.C. Guards  17.392977  78.456867   
57                             A.C. Guards  17.392977  78.456867   
58                

In [38]:
venues_df.groupby("Neighborhood").count()

Latitude  Longitude  Venuename  \
Neighborhood                                                           
A. S. Rao Nagar                             24         24         24   
A.C. Guards                                 48         48         48   
Abhyudaya Nagar                             10         10         10   
Abids                                       81         81         81   
Adikmet                                     21         21         21   
Afzal Gunj                                  48         48         48   
Aghapura                                    54         54         54   
Aliabad, Hyderabad                           9          9          9   
Alijah Kotla                                14         14         14   
Allwyn Colony                               14         14         14   
Alwal                                        4          4          4   
Amberpet                                    17         17         17   
Ameerpet                                   100        100        100   
Ashok Nagar, Hyderabad                      70         70         70   
Asif Nagar                                  15         15         15   
Attapur                                      5          5          5   
Azamabad, Hyderabad                         46         46         46   
Azampura                                    23         23         23   
BHEL Township, Hyderabad                     5          5          5   
BJR Nagar                                   55         55         55   
Badichowdi                                  72         72         72   
Bagh Lingampally                            47         47         47   
Bairamalguda                                 8          8          8   
Balkampet                                   51         51         51   
Banjara Hills                              100        100        100   
Bank Street, Hyderabad                      80         80         80   
Barkas, Hyderabad                            7          7          7   
Barkatpura                                  43         43         43   
Basheerbagh                                 97         97         97   
Bazarghat                                   88         88         88   
Begum Bazaar                                29         29         29   
Begumpet                                    53         53         53   
Bharat Nagar                                 5          5          5   
Boggulkunta                                 84         84         84   
Borabanda                                   13         13         13   
Bowenpally                                  23         23         23   
Brahman Vaadi                               17         17         17   
Chaderghat                                  38         38         38   
Champapet                                    5          5          5   
Chanchalguda                                13         13         13   
Chandrayan Gutta                            11         11         11   
Chatta Bazaar                               26         26         26   
Cherlapally                                  4          4          4   
Chikkadpally                                64         64         64   
Chilkalguda                                 19         19         19   
Chintal Basti                              100        100        100   
Chintalakunta                                8          8          8   
Dabirpura                                   19         19         19   
Dar-ul-Shifa                                30         30         30   
Dhoolpet                                    14         14         14   
Dilsukhnagar                                22         22         22   
Domalguda                                   83         83         83   
ECIL 'X' Roads                               5          5          5   
Edi Bazar                                    6          6          6   
Erraga

In [39]:
print('There are {} uniques categories.'.format(len(venues_df['VenueCategory'].unique())))


There are 170 uniques categories.


In [41]:

venues_df['VenueCategory'].unique()[:50]

array(['Indian Restaurant', 'Movie Theater', 'Sandwich Place',
       'Convenience Store', 'Ice Cream Shop', 'Coffee Shop', 'Café',
       'Asian Restaurant', 'Park', 'Chinese Restaurant', 'Bakery',
       'Hyderabadi Restaurant', 'Juice Bar', 'Lounge',
       'South Indian Restaurant', 'Bistro', 'Science Museum',
       'Snack Place', 'Middle Eastern Restaurant',
       'Vegetarian / Vegan Restaurant', 'Stadium',
       'Performing Arts Venue', 'Hotel', 'Hotel Bar',
       'Fast Food Restaurant', 'Pizza Place', 'Mobile Phone Shop',
       'Fried Chicken Joint', 'Department Store', 'Hookah Bar',
       'Electronics Store', 'Clothing Store', 'Restaurant', 'Shoe Store',
       'Food Truck', 'Neighborhood', 'Chaat Place', 'Diner',
       'Burger Joint', 'Dessert Shop', 'Smoke Shop', 'Breakfast Spot',
       'Bar', 'Shopping Mall', 'Food', 'Multiplex', 'Gaming Cafe',
       'Indie Movie Theater', 'Farmers Market', 'Food Court'],
      dtype=object)

In [46]:
# check if the results contain "Restaurant"

"Restaurant" in venues_df['VenueCategory'].unique()


True

## Analyze each neighborhood

In [49]:
hyd_onehot=pd.get_dummies(venues_df["VenueCategory"],prefix="",prefix_sep="")

# add neighborhood column back to dataframe
hyd_onehot['Neighborhoods'] = venues_df['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [hyd_onehot.columns[-1]] + list(hyd_onehot.columns[:-1])
hyd_onehot = hyd_onehot[fixed_columns]

print(hyd_onehot.shape)
hyd_onehot.head()

(6769, 171)


Neighborhoods  ATM  Accessories Store  Afghan Restaurant  \
0  A. S. Rao Nagar    0                  0                  0   
1  A. S. Rao Nagar    0                  0                  0   
2  A. S. Rao Nagar    0                  0                  0   
3  A. S. Rao Nagar    0                  0                  0   
4  A. S. Rao Nagar    0                  0                  0   

   American Restaurant  Andhra Restaurant  Arcade  Arts & Crafts Store  \
0                    0                  0       0                    0   
1                    0                  0       0                    0   
2                    0                  0       0                    0   
3                    0                  0       0                    0   
4                    0                  0       0                    0   

   Asian Restaurant  Athletics & Sports  Auditorium  BBQ Joint  \
0                 0                   0           0          0   
1                 0                   0           0          0   
2                 0                   0           0          0   
3                 0                   0           0          0   
4                 0                   0           0          0   

   Badminton Court  Bakery  Bank  Bar  Baseball Field  Bed & Breakfast  \
0                0       0     0    0               0                0   
1                0       0     0    0               0                0   
2                0       0     0    0               0                0   
3                0       0     0    0               0                0   
4                0       0     0    0               0                0   

   Beer Garden  Bengali Restaurant  Big Box Store  Bike Rental / Bike Share  \
0            0                   0              0                         0   
1            0                   0              0                         0   
2            0                   0              0                         0   
3            0                   0              0                         0   
4            0                   0              0                         0   

   Bistro  Bookstore  Boutique  Bowling Alley  Breakfast Spot  Brewery  \
0       0          0         0              0               0        0   
1       0          0         0              0               0        0   
2       0          0         0              0               0        0   
3       0          0         0              0               0        0   
4       0          0         0              0               0        0   

   Buffet  Burger Joint  Bus Station  Business Service  Butcher  Cable Car  \
0       0             0            0                 0        0          0   
1       0             0            0                 0        0          0   
2       0             0            0                 0        0          0   
3       0             0            0                 0        0          0   
4       0             0            0                 0        0          0   

   Café  Campground  Chaat Place  Chinese Restaurant  Chocolate Shop  \
0     0           0            0                   0               0   
1     0           0            0                   0               0   
2     0           0            0                   0               0   
3     0           0            0                   0               0   
4     0           0            0                   0               0   

   Clothing Store  Cocktail Bar  Coffee Shop  Comfort Food Restaurant  \
0               0             0            0                        0   
1               0             0            0                        0   
2               0             0            0                        0   
3               0             0            0                        0   
4               0             0            0                        0   

   Concert Hall  Convenience Store  Cricket Ground  Cupcake Shop  

In [51]:
hyd_grouped=hyd_onehot.groupby("Neighborhoods").mean().reset_index()

print(hyd_grouped.shape)
hyd_grouped

(200, 171)


Neighborhoods       ATM  Accessories Store  \
0                         A. S. Rao Nagar  0.000000           0.000000   
1                             A.C. Guards  0.000000           0.000000   
2                         Abhyudaya Nagar  0.000000           0.000000   
3                                   Abids  0.000000           0.000000   
4                                 Adikmet  0.000000           0.000000   
5                              Afzal Gunj  0.000000           0.000000   
6                                Aghapura  0.000000           0.000000   
7                      Aliabad, Hyderabad  0.000000           0.000000   
8                            Alijah Kotla  0.000000           0.000000   
9                           Allwyn Colony  0.000000           0.000000   
10                                  Alwal  0.250000           0.000000   
11                               Amberpet  0.000000           0.000000   
12                               Ameerpet  0.000000           0.000000   
13                 Ashok Nagar, Hyderabad  0.000000           0.000000   
14                             Asif Nagar  0.000000           0.000000   
15                                Attapur  0.000000           0.000000   
16                    Azamabad, Hyderabad  0.000000           0.000000   
17                               Azampura  0.000000           0.000000   
18               BHEL Township, Hyderabad  0.000000           0.000000   
19                              BJR Nagar  0.000000           0.000000   
20                             Badichowdi  0.000000           0.000000   
21                       Bagh Lingampally  0.000000           0.000000   
22                           Bairamalguda  0.000000           0.000000   
23                              Balkampet  0.000000           0.000000   
24                          Banjara Hills  0.000000           0.000000   
25                 Bank Street, Hyderabad  0.000000           0.000000   
26                      Barkas, Hyderabad  0.000000           0.000000   
27                             Barkatpura  0.000000           0.000000   
28                            Basheerbagh  0.000000           0.000000   
29                              Bazarghat  0.000000           0.000000   
30                           Begum Bazaar  0.000000           0.000000   
31                               Begumpet  0.000000           0.000000   
32                           Bharat Nagar  0.600000           0.000000   
33                            Boggulkunta  0.000000           0.000000   
34                              Borabanda  0.000000           0.000000   
35                             Bowenpally  0.000000           0.000000   
36                          Brahman Vaadi  0.000000           0.000000   
37                             Chaderghat  0.000000           0.000000   
38                              Champapet  0.000000           0.000000   
39                           Chanchalguda  0.000000           0.000000   
40                       Chandrayan Gutta  0.000000           0.000000   
41                          Chatta Bazaar  0.000000           0.000000   
42                            Cherlapally  0.250000           0.000000   
43                           Chikkadpally  0.000000           0.000000   
44                            Chilkalguda  0.000000           0.000000   
45                          Chintal Basti  0.000000           0.000000   
46                          Chintalakunta  0.000000           0.000000   
47                              Dabirpura  0.000000           0.000000   
48                           Dar-ul-Shifa  0.000000           0.000000   
49                               Dhoolpet  0.000000           0.000000   
50                           Dilsukhnagar  0.000000           0.000000   
51                              Domalguda  0.000000           0.000000   
52                         ECIL 'X' Roads  0.000000           0.000000   
53                              

In [63]:
len(hyd_grouped[hyd_grouped["Indian Restaurant"]>0])

                        

167

In [65]:
hyd_res=hyd_grouped[["Neighborhoods","Indian Restaurant"]]
hyd_res

Neighborhoods  Indian Restaurant
0                         A. S. Rao Nagar           0.291667
1                             A.C. Guards           0.166667
2                         Abhyudaya Nagar           0.000000
3                                   Abids           0.123457
4                                 Adikmet           0.333333
5                              Afzal Gunj           0.083333
6                                Aghapura           0.166667
7                      Aliabad, Hyderabad           0.222222
8                            Alijah Kotla           0.071429
9                           Allwyn Colony           0.214286
10                                  Alwal           0.000000
11                               Amberpet           0.176471
12                               Ameerpet           0.150000
13                 Ashok Nagar, Hyderabad           0.114286
14                             Asif Nagar           0.266667
15                                Attapur           0.000000
16                    Azamabad, Hyderabad           0.217391
17                               Azampura           0.086957
18               BHEL Township, Hyderabad           0.400000
19                              BJR Nagar           0.054545
20                             Badichowdi           0.125000
21                       Bagh Lingampally           0.212766
22                           Bairamalguda           0.000000
23                              Balkampet           0.254902
24                          Banjara Hills           0.080000
25                 Bank Street, Hyderabad           0.112500
26                      Barkas, Hyderabad           0.000000
27                             Barkatpura           0.209302
28                            Basheerbagh           0.113402
29                              Bazarghat           0.147727
30                           Begum Bazaar           0.103448
31                               Begumpet           0.245283
32                           Bharat Nagar           0.000000
33                            Boggulkunta           0.130952
34                              Borabanda           0.076923
35                             Bowenpally           0.086957
36                          Brahman Vaadi           0.176471
37                             Chaderghat           0.105263
38                              Champapet           0.200000
39                           Chanchalguda           0.076923
40                       Chandrayan Gutta           0.090909
41                          Chatta Bazaar           0.076923
42                            Cherlapally           0.000000
43                           Chikkadpally           0.171875
44                            Chilkalguda           0.157895
45                          Chintal Basti           0.130000
46                          Chintalakunta           0.000000
47                              Dabirpura           0.105263
48                           Dar-ul-Shifa           0.133333
49                               Dhoolpet           0.071429
50                           Dilsukhnagar           0.181818
51                              Domalguda           0.132530
52                         ECIL 'X' Roads           0.400000
53                              Edi Bazar           0.166667
54                              Erragadda           0.125000
55                 Fateh Nagar, Hyderabad           0.125000
56                              Ferozguda           0.000000
57                             Film Nagar           0.074627
58                             Gachibowli           0.170000
59                           Gaddiannaram           0.117647
60                                Golnaka           0.205882
61                             Goshamahal           0.113636
62                           Gudimalkapur           0.272727
63                            Gulzar Houz           0.066667
64                             HITEC City           0.177215
65

## Cluster neighborhoods

In [72]:
k_clusters=3

hyd_clust=hyd_grouped.drop(["Neighborhoods"],axis=1)

# run k-means clustering
kmeans = KMeans(n_clusters=k_clusters,init = "k-means++", random_state=0).fit(hyd_clust)

# check cluster labels generated for each row in the dataframe
kmeans.labels_



array([1, 0, 0, 0, 1, 0, 0, 1, 0, 1, 2, 1, 0, 0, 1, 0, 1, 0, 1, 0, 0, 1,
       0, 1, 0, 0, 0, 1, 0, 0, 0, 1, 2, 0, 0, 0, 1, 0, 1, 0, 0, 0, 2, 1,
       0, 0, 0, 0, 0, 0, 1, 0, 1, 1, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 1, 1,
       1, 0, 0, 2, 0, 0, 2, 0, 1, 0, 1, 2, 0, 1, 1, 1, 0, 0, 0, 1, 0, 0,
       0, 0, 1, 1, 1, 1, 0, 0, 1, 0, 0, 1, 0, 1, 1, 0, 1, 0, 1, 1, 0, 0,
       1, 0, 0, 1, 0, 0, 1, 0, 0, 2, 0, 0, 0, 0, 0, 0, 1, 1, 0, 0, 2, 0,
       0, 0, 0, 0, 0, 1, 0, 1, 0, 1, 0, 1, 0, 0, 0, 1, 0, 1, 0, 1, 0, 0,
       0, 1, 0, 0, 1, 2, 0, 0, 0, 0, 0, 2, 0, 1, 1, 1, 0, 0, 0, 0, 1, 0,
       0, 0, 0, 0, 1, 0, 0, 1, 0, 0, 1, 1, 1, 0, 1, 0, 0, 0, 1, 0, 0, 0,
       0, 0])

In [73]:
hyd_merged=hyd_res.copy()

#add cluster labels

hyd_merged["Cluster Labels"]=kmeans.labels_

In [79]:
hyd_merged.rename(columns={"Neighborhoods":"Neighborhood"},inplace=True)
hyd_merged.head()

Neighborhood  Indian Restaurant  Cluster Labels
0  A. S. Rao Nagar           0.291667               1
1      A.C. Guards           0.166667               0
2  Abhyudaya Nagar           0.000000               0
3            Abids           0.123457               0
4          Adikmet           0.333333               1

In [81]:
hyd_merged["Latitude"]=hyd_df["Latitude"]
hyd_merged["Longitude"]=hyd_df["Longitude"]
hyd_merged.shape

(200, 5)

In [85]:
hyd_merged.sort_values(["Cluster Labels"], inplace=True)
hyd_merged


Neighborhood  Indian Restaurant  Cluster Labels  \
199                         Sitaphalmandi           0.136364               0   
142                    Nalgonda 'X' Roads           0.043478               0   
5                              Afzal Gunj           0.083333               0   
6                                Aghapura           0.166667               0   
196                          Sikh Village           0.142857               0   
8                            Alijah Kotla           0.071429               0   
195                       Shyam Rao Nagar           0.133333               0   
193                          Shanker Mutt           0.125000               0   
12                               Ameerpet           0.150000               0   
13                 Ashok Nagar, Hyderabad           0.114286               0   
192                        Shahran Market           0.062500               0   
191                        Shah-Ali-Banda           0.062500               0   
35                             Bowenpally           0.086957               0   
17                               Azampura           0.086957               0   
20                             Badichowdi           0.125000               0   
3                                   Abids           0.123457               0   
189                          Secunderabad           0.107692               0   
24                          Banjara Hills           0.080000               0   
25                 Bank Street, Hyderabad           0.112500               0   
26                      Barkas, Hyderabad           0.000000               0   
28                            Basheerbagh           0.113402               0   
29                              Bazarghat           0.147727               0   
30                           Begum Bazaar           0.103448               0   
33                            Boggulkunta           0.130952               0   
34                              Borabanda           0.076923               0   
175                             Rani Gunj           0.123288               0   
70                Himayatnagar, Hyderabad           0.138298               0   
173                           Ramanthapur           0.000000               0   
19                              BJR Nagar           0.054545               0   
2                         Abhyudaya Nagar           0.000000               0   
22                           Bairamalguda           0.000000               0   
55                 Fateh Nagar, Hyderabad           0.125000               0   
44                            Chilkalguda           0.157895               0   
182                              Saifabad           0.103093               0   
46                          Chintalakunta           0.000000               0   
59                           Gaddiannaram           0.117647               0   
177                  Red Hills, Hyderabad           0.139535               0   
181                              Saidabad           0.062500               0   
63                            Gulzar Houz           0.066667               0   
61                             Goshamahal           0.113636               0   
176                      Rastrapathi Road           0.146667               0   
41                          Chatta Bazaar           0.076923               0   
40                       Chandrayan Gutta           0.090909               0   
122                       Manovikas Nagar           0.050000               0   
39                           Chanchalguda           0.076923               0   
197                   Silpa Avenue Colony           0.131579               0   
37                             Chaderghat           0.105263               0   
47                              Dabirpura           0.105263               0   
57                             Film Nagar           0.074627               0   
48                           

In [87]:
hyd_merged["Cluster Labels"].value_counts()

0    125
1     65
2     10
Name: Cluster Labels, dtype: int64

## analyze  cluster results in map

In [89]:
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(k_clusters)
ys = [i+x+(i*x)**2 for i in range(k_clusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(hyd_merged['Latitude'],hyd_merged['Longitude'], hyd_merged['Neighborhood'], hyd_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [90]:
map_clusters.save('map_clusters.html')


## Examine Clusters

### Cluster 1

In [93]:
hyd_merged.loc[hyd_merged["Cluster Labels"]==0]

Neighborhood  Indian Restaurant  Cluster Labels  \
199                         Sitaphalmandi           0.136364               0   
142                    Nalgonda 'X' Roads           0.043478               0   
5                              Afzal Gunj           0.083333               0   
6                                Aghapura           0.166667               0   
196                          Sikh Village           0.142857               0   
8                            Alijah Kotla           0.071429               0   
195                       Shyam Rao Nagar           0.133333               0   
193                          Shanker Mutt           0.125000               0   
12                               Ameerpet           0.150000               0   
13                 Ashok Nagar, Hyderabad           0.114286               0   
192                        Shahran Market           0.062500               0   
191                        Shah-Ali-Banda           0.062500               0   
35                             Bowenpally           0.086957               0   
17                               Azampura           0.086957               0   
20                             Badichowdi           0.125000               0   
3                                   Abids           0.123457               0   
189                          Secunderabad           0.107692               0   
24                          Banjara Hills           0.080000               0   
25                 Bank Street, Hyderabad           0.112500               0   
26                      Barkas, Hyderabad           0.000000               0   
28                            Basheerbagh           0.113402               0   
29                              Bazarghat           0.147727               0   
30                           Begum Bazaar           0.103448               0   
33                            Boggulkunta           0.130952               0   
34                              Borabanda           0.076923               0   
175                             Rani Gunj           0.123288               0   
70                Himayatnagar, Hyderabad           0.138298               0   
173                           Ramanthapur           0.000000               0   
19                              BJR Nagar           0.054545               0   
2                         Abhyudaya Nagar           0.000000               0   
22                           Bairamalguda           0.000000               0   
55                 Fateh Nagar, Hyderabad           0.125000               0   
44                            Chilkalguda           0.157895               0   
182                              Saifabad           0.103093               0   
46                          Chintalakunta           0.000000               0   
59                           Gaddiannaram           0.117647               0   
177                  Red Hills, Hyderabad           0.139535               0   
181                              Saidabad           0.062500               0   
63                            Gulzar Houz           0.066667               0   
61                             Goshamahal           0.113636               0   
176                      Rastrapathi Road           0.146667               0   
41                          Chatta Bazaar           0.076923               0   
40                       Chandrayan Gutta           0.090909               0   
122                       Manovikas Nagar           0.050000               0   
39                           Chanchalguda           0.076923               0   
197                   Silpa Avenue Colony           0.131579               0   
37                             Chaderghat           0.105263               0   
47                              Dabirpura           0.105263               0   
57                             Film Nagar           0.074627               0   
48                           

## cluster 2

In [94]:
hyd_merged.loc[hyd_merged["Cluster Labels"]==1]

Neighborhood  Indian Restaurant  Cluster Labels   Latitude  \
116                    Malakpet           0.214286               1  17.374930   
11                     Amberpet           0.176471               1  17.385820   
4                       Adikmet           0.333333               1  17.410610   
126                 Mehdipatnam           0.264151               1  17.392630   
180                   Safilguda           0.230769               1  17.466430   
14                   Asif Nagar           0.266667               1  17.385140   
137                 Musheerabad           0.214286               1  17.414690   
7            Aliabad, Hyderabad           0.222222               1  17.342590   
76                Jamia Osmania           0.214286               1  17.421963   
99                 Lab quarters           0.169811               1  17.490517   
79                    Kachiguda           0.212766               1  17.386880   
74                     Jahanuma           0.222222               1  17.341389   
96                   Kukatpally           0.181818               1  17.487350   
9                 Allwyn Colony           0.214286               1  17.503370   
18     BHEL Township, Hyderabad           0.400000               1  17.388970   
106      Lingampally, Hyderabad           0.197183               1  17.396690   
113                  Madinaguda           0.187500               1  17.493000   
110                 Madeenaguda           0.187500               1  17.493000   
21             Bagh Lingampally           0.212766               1  17.448510   
90   Kings Colony, Shastripuram           0.200000               1  17.325980   
91                     Kompally           0.250000               1  17.533180   
92                     Kondapur           0.272727               1  17.466600   
81      Kamala Nagar, Hyderabad           0.173913               1  17.365610   
93          Kothapet, Hyderabad           0.277778               1  17.368830   
85                       Karwan           0.266667               1  17.379070   
102                 Lal Darwaza           0.250000               1  17.342267   
101           Lal Bahadur Nagar           0.272727               1  17.377630   
104                 Langar Houz           0.166667               1  17.382085   
127                   Mettuguda           0.285714               1  17.427740   
80               Kakatiya Nagar           0.142857               1  17.410990   
107                 Lingojiguda           0.200000               1  17.350670   
23                    Balkampet           0.254902               1  17.388592   
169         Radha Krishna Nagar           0.200000               1  17.425110   
31                     Begumpet           0.245283               1  17.505990   
155     Padmanabha Nagar Colony           0.200000               1  17.391590   
151                    Neredmet           0.142857               1  17.477177   
174         Ramnagar, Hyderabad           0.291667               1  17.432250   
186        Sanjeeva Reddy Nagar           0.191781               1  17.444380   
27                   Barkatpura           0.209302               1  17.398103   
187                Santoshnagar           0.225000               1  17.392100   
149           Nawab Saheb Kunta           0.142857               1  17.339340   
167                Quthbullapur           0.230769               1  17.505360   
147                  Nanalnagar           0.173913               1  17.394450   
183                  Sainikpuri           0.142857               1  17.477177   
16          Azamabad, Hyderabad           0.217391               1  17.407100   
168                 RTC X Roads           0.400000               1  17.458160   
188                 Saroornagar           0.166667               1  17.354420   
158                  Parsigutta           0.280000               1  17.416630   
139                    Nacharam           0.200000

## cluster 3

In [95]:
hyd_merged.loc[hyd_merged["Cluster Labels"]==2]

Neighborhood  Indian Restaurant  Cluster Labels   Latitude  Longitude
42    Cherlapally                0.0               2  17.466480  78.599990
77     Jeedimetla                0.0               2  17.521830  78.454330
159    Patancheru                0.0               2  17.526770  78.252340
32   Bharat Nagar                0.0               2  17.412570  78.405190
130       Miyapur                0.0               2  17.421020  78.582440
10          Alwal                0.0               2  17.535430  78.544270
165    Purana pul                0.0               2  17.310671  78.439025
119      Mallapur                0.0               2  17.450017  78.609361
69    Hayathnagar                0.0               2  17.404860  78.481210
72   IDA Bollaram                0.0               2  17.554030  78.344590

## Observations


Most of the Indian Restaurants are concentrated in the central area of hyderabad city, with the highest number in cluster 1 and moderate number in cluster 2. On the other hand, cluster 3 has very low number to totally no indian restaurants in the neighborhoods. This represents a great opportunity and high potential areas to open new indian restaurant as there is very little to no competition from existing restaurants. Meanwhile, indian restaurants in cluster 2 are likely suffering from intense competition due to oversupply and high concentration of restaurants. From another perspective, this also shows that the oversupply of restaurants mostly happened in the central area of the city, with the suburb area still have very few indian restaurants. Therefore, this project recommends property developers to capitalize on these findings to open new indian restaurants in neighborhoods in cluster 3 with little to no competition. Property developers with unique selling propositions to stand out from the competition can also open new restaurants in neighborhoods in cluster 2 with moderate competition. Lastly, property developers are advised to avoid neighborhoods in cluster 1 which already have high concentration of shopping malls and suffering from intense competition